# Intelligent Agents: Reflex-Based Agents for the Vacuum-cleaner World


## Instructions

Total Points: Undergrads 100 / Graduate students 110

Complete this notebook. Use the provided notebook cells and insert additional code and markdown cells as needed. Submit the completely rendered notebook as a PDF file. 

## Introduction

In this assignment you will implement a simulator environment for an automatic vacuum cleaner robot, a set of different reflex-based agent programs, and perform a comparison study for cleaning a single room. Focus on the __cleaning phase__ which starts when the robot is activated and ends when the last dirty square in the room has been cleaned. Someone else will take care of the agent program needed to navigate back to the charging station after the room is clean.

## PEAS description of the cleaning phase

__Performance Measure:__ Each action costs 1 energy unit. The performance is measured as the sum of the energy units used to clean the whole room.

__Environment:__ A room with $n \times n$ squares where $n = 5$. Dirt is randomly placed on each square with probability $p = 0.2$. For simplicity, you can assume that the agent knows the size and the layout of the room (i.e., it knows $n$). To start, the agent is placed on a random square.

__Actuators:__ The agent can clean the current square (action `suck`) or move to an adjacent square by going `north`, `east`, `south`, or `west`.

__Sensors:__ Four bumper sensors, one for north, east, south, and west; a dirt sensor reporting dirt in the current square.  


## The agent program for a simple randomized agent

The agent program is a function that gets sensor information (the current percepts) as the arguments. The arguments are:

* A dictionary with boolean entries for the for bumper sensors `north`, `east`, `west`, `south`. E.g., if the agent is on the north-west corner, `bumpers` will be `{"north" : True, "east" : False, "south" : False, "west" : True}`.
* The dirt sensor produces a boolean.

The agent returns the chosen action as a string.

Here is an example implementation for the agent program of a simple randomized agent:  

In [1]:
import numpy as np

actions = ["north", "east", "west", "south", "suck"]

def simple_randomized_agent(bumpers, dirty):
    return np.random.choice(actions)

In [2]:
# define percepts (current location is NW corner and it is dirty)
bumpers = {"north" : True, "east" : False, "south" : False, "west" : True}
dirty = True

# call agent program function with percepts and it returns an action
simple_randomized_agent(bumpers, dirty)

'north'

__Note:__ This is not a rational intelligent agent. It ignores its sensors and may bump into a wall repeatedly or not clean a dirty square. You will be asked to implement rational agents below.

## Simple environment example

We implement a simple simulation environment that supplies the agent with its percepts.
The simple environment is infinite in size (bumpers are always `False`) and every square is always dirty, even if the agent cleans it. The environment function returns a performance measure which is here the number of cleaned squares (since the room is infinite and all squares are constantly dirty, the agent can never clean the whole room as required in the PEAS description above). The energy budget of the agent is specified as `max_steps`. 

In [3]:
def simple_environment(agent, max_steps, verbose = True):
    num_cleaned = 0
    
    for i in range(max_steps):
        dirty = True
        bumpers = {"north" : False, "south" : False, "west" : False, "east" : False}

        action = agent(bumpers, dirty)
        if (verbose): print("step", i , "- action:", action) 
        
        if (action == "suck"): 
            num_cleaned = num_cleaned + 1
        
    return num_cleaned
        


Do one simulation run with a simple randomized agent that has enough energy for 20 steps.

In [4]:
simple_environment(simple_randomized_agent, max_steps = 20)

step 0 - action: west
step 1 - action: west
step 2 - action: west
step 3 - action: south
step 4 - action: west
step 5 - action: east
step 6 - action: east
step 7 - action: south
step 8 - action: suck
step 9 - action: north
step 10 - action: suck
step 11 - action: east
step 12 - action: suck
step 13 - action: south
step 14 - action: west
step 15 - action: east
step 16 - action: south
step 17 - action: west
step 18 - action: south
step 19 - action: south


3

# Tasks

## General [10 Points]

1. Make sure that you use the latest version of this notebook. Sync your forked repository and pull the latest revision. 
2. Your implementation can use libraries like math, numpy, scipy, but not libraries that implement inteligent agents or complete search algorithms. Try to keep the code simple! In this course, we want to learn about the algorithms and we often do not need to use object-oriented design.
3. You notebook needs to be formated professionally. 
    - Add additional markdown blocks for your description, comments in the code, add tables and use mathplotlib to produce charts where appropriate
    - Do not show debugging output or include an excessive amount of output.
    - Check that your PDF file is readable. For example, long lines are cut off in the PDF file. You don't have control over page breaks, so do not worry about these.
4. Document your code. Add a short discussion of how your implementation works and your design choices.


## Task 1: Implement a simulation environment [20 Points]

The simple environment above is not very realistic. Your environment simulator needs to follow the PEAS description from above. It needs to:

* Initialize the environment by storing the state of each square (clean/dirty) and making some dirty. ([Help with random numbers and arrays in Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/random_numbers_and_arrays.ipynb))
* Keep track of the agent's position.
* Call the agent function repeatedly and provide the agent function with the sensor inputs.  
* React to the agent's actions. E.g, by removing dirt from a square or moving the agent around unless there is a wall in the way.
* Keep track of the performance measure. That is, track the agent's actions until all dirty squares are clean and count the number of actions it takes the agent to complete the task.

The easiest implementation for the environment is to hold an 2-dimensional array to represent if squares are clean or dirty and to call the agent function in a loop until all squares are clean or a predefined number of steps have been reached (i.e., the robot runs out of energy).

The simulation environment should be a function like the `simple_environment()` and needs to work with the simple randomized agent program from above. **Use the same environmnt for all your agent implementations in the tasks below.**

*Note on debugging:* Debugging is difficult. Make sure your environment prints enough information when you use `verbose = True`. Also, implementing a function that the environment can use to displays the room with dirt and the current position of the robot at every step is very useful.  

In [5]:
def bumper_sensors(n, position_x, position_y, verbose=True):
    
    bumpers = {"north": False, "south": False, "west": False, "east": False}
    
    # If East
    if(position_x == n-1):
        # If Northeast
        if(position_y == 0):
            return {"north" : True, "south" : False, "west" : False, "east" : True}
        
        # If Southeast
        elif(position_y == n-1):
            return {"north" : False, "south" : True, "west" : False, "east" : True}
        
        # If Only East
        else:
            return {"north" : False, "south" : False, "west" : False, "east" : True}
    
    # If West
    elif(position_x == 0):
        if(position_y == 0):
            return {"north" : True, "south" : False, "west" : True, "east" : False}
        elif(position_y == n-1):
            return {"north" : False, "south" : True, "west" : True, "east" : False}
        else:
            return{ "north" : False, "south" : False, "west" : True, "east" : False}
    
    # If only North or only South
    if(position_y == 0):
        return {"north" : True, "south" : False, "west" : False, "east" : False}
    elif(position_y == n-1):
        return{"north" : False, "south" : True, "west" : False, "east" : False}

    return bumpers




In [6]:
# Your code and description goes here
def simulation_environment(agent, n, verbose = True): 
    num_cleaned = 0 # Keeping track of swaures cleaned
    num_actions_total = 0
    rng = np.random.default_rng() # create random number generator
    p = 0.2 # use given probability from instructions
    squares = [[rng.random() < p for x in range(n)] for y in range(n)] # intitalize squares array w/ clean and dirty squares
    count_dirty = np.count_nonzero(squares)
    print("Number of dirty squares:")
    print(count_dirty)
    position_x = rng.integers(low = 0, high = n-1)
    position_y = rng.integers(low = 0, high = n-1)
    dirty = squares[position_x][position_y]
    bumpers = bumper_sensors(n, position_x, position_y)
    print(bumpers)
    
    while(count_dirty != 0):
        action = agent(bumpers, dirty)
        
        if (verbose): print("Environment: Step", num_actions_total , "- action:", action, " position: (", position_x, ",", position_y, ")")
        num_actions_total += 1

        if(action == "west"):
            position_x -= 1
            if(position_x < 0):
                position_x = 0
            
        if(action == "east"):
            position_x += 1
            if(position_x > n-1):
                position_x = n-1
            

        if(action == "north"):
            position_y -= 1
            if(position_y < 0):
                position_y = 0
                
        if(action == "south"):
            position_y += 1
            if(position_y > n-1):
                position_y = n-1
        
        if (action == "suck" and squares[position_x][position_y] == True):
            squares[position_x][position_y] = False
            num_cleaned = num_cleaned + 1
            count_dirty = np.count_nonzero(squares)
            
        dirty = squares[position_x][position_y]
        bumpers = bumper_sensors(n, position_x, position_y)
        
    print("Total number of actions: ")
    print(num_actions_total)
    for i in range(n):
        print(squares[i])

    print("Final Position - (", position_x, ",", position_y, ")")
    print("Number of squares cleaned: ")    
    return num_cleaned
        
    


In [7]:
simulation_environment(simple_randomized_agent, 5)

Number of dirty squares:
6
{'north': False, 'south': False, 'west': False, 'east': False}
Environment: Step 0 - action: west  position: ( 1 , 2 )
Environment: Step 1 - action: west  position: ( 0 , 2 )
Environment: Step 2 - action: suck  position: ( 0 , 2 )
Environment: Step 3 - action: east  position: ( 0 , 2 )
Environment: Step 4 - action: suck  position: ( 1 , 2 )
Environment: Step 5 - action: east  position: ( 1 , 2 )
Environment: Step 6 - action: suck  position: ( 2 , 2 )
Environment: Step 7 - action: west  position: ( 2 , 2 )
Environment: Step 8 - action: north  position: ( 1 , 2 )
Environment: Step 9 - action: suck  position: ( 1 , 1 )
Environment: Step 10 - action: east  position: ( 1 , 1 )
Environment: Step 11 - action: suck  position: ( 2 , 1 )
Environment: Step 12 - action: south  position: ( 2 , 1 )
Environment: Step 13 - action: east  position: ( 2 , 2 )
Environment: Step 14 - action: east  position: ( 3 , 2 )
Environment: Step 15 - action: south  position: ( 4 , 2 )
Envir

Environment: Step 150 - action: south  position: ( 0 , 1 )
Environment: Step 151 - action: suck  position: ( 0 , 2 )
Environment: Step 152 - action: suck  position: ( 0 , 2 )
Environment: Step 153 - action: west  position: ( 0 , 2 )
Environment: Step 154 - action: north  position: ( 0 , 2 )
Environment: Step 155 - action: west  position: ( 0 , 1 )
Environment: Step 156 - action: north  position: ( 0 , 1 )
Environment: Step 157 - action: east  position: ( 0 , 0 )
Environment: Step 158 - action: suck  position: ( 1 , 0 )
Environment: Step 159 - action: east  position: ( 1 , 0 )
Environment: Step 160 - action: north  position: ( 2 , 0 )
Environment: Step 161 - action: south  position: ( 2 , 0 )
Environment: Step 162 - action: east  position: ( 2 , 1 )
Environment: Step 163 - action: suck  position: ( 3 , 1 )
Environment: Step 164 - action: south  position: ( 3 , 1 )
Environment: Step 165 - action: suck  position: ( 3 , 2 )
Environment: Step 166 - action: south  position: ( 3 , 2 )
Environ

6

## Task 2:  Implement a simple reflex agent [10 Points] 

The simple reflex agent randomly walks around but reacts to the bumper sensor by not bumping into the wall and to dirt with sucking. Implement the agent program as a function.

_Note:_ Agents cannot directly use variable in the environment. They only gets the percepts as the arguments to the agent function.

In [8]:
# Your code and description goes here
def simple_reflex_agent(bumpers, dirty):
    if(dirty == True):
        return "suck" # return suck
    if(bumpers.get("north") == True):
        return "south"
    if(bumpers.get("south") == True):
        return "north"
    if(bumpers.get("east") == True):
        return "west"
    if(bumpers.get("west") == True):
        return "east"

    return np.random.choice(actions)

In [9]:
simulation_environment(simple_reflex_agent, 5)

Number of dirty squares:
5
{'north': False, 'south': False, 'west': False, 'east': False}
Environment: Step 0 - action: north  position: ( 2 , 3 )
Environment: Step 1 - action: suck  position: ( 2 , 2 )
Environment: Step 2 - action: north  position: ( 2 , 2 )
Environment: Step 3 - action: north  position: ( 2 , 1 )
Environment: Step 4 - action: south  position: ( 2 , 0 )
Environment: Step 5 - action: east  position: ( 2 , 1 )
Environment: Step 6 - action: west  position: ( 3 , 1 )
Environment: Step 7 - action: north  position: ( 2 , 1 )
Environment: Step 8 - action: south  position: ( 2 , 0 )
Environment: Step 9 - action: west  position: ( 2 , 1 )
Environment: Step 10 - action: east  position: ( 1 , 1 )
Environment: Step 11 - action: west  position: ( 2 , 1 )
Environment: Step 12 - action: west  position: ( 1 , 1 )
Environment: Step 13 - action: suck  position: ( 0 , 1 )
Environment: Step 14 - action: east  position: ( 0 , 1 )
Environment: Step 15 - action: suck  position: ( 1 , 1 )
En

5

## Task 3: Implement a model-based reflex agent [20 Points]

Model-based agents use a state to keep track of what they have done and perceived so far. Your agent needs to find out where it is located and then keep track of its current location. You also need a set of rules based on the state and the percepts to make sure that the agent will clean the whole room. For example, the agent can move to a corner to determine its location and then it can navigate through the whole room and clean dirty squares.

Describe how you define the __agent state__ and how your agent works before implementing it. ([Help with implementing state information on Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/store_agent_state_information.ipynb))

In [10]:
# Your short description of the state and your implementation goes here
# Going into the room, the agent will assume that the entire room is dirty...


In [11]:
phase_one = False
cleaned = []
row = -1
col = -1
direction = "east"

def Model_Based_Reflex(bumpers, dirty):
    global phase_one
    global direction
    global clean
    global row
    global col

    if(phase_one == False):
        if(bumpers.get("north") == True and bumpers.get("west") == True):
            phase_one = True
            print("\tAgent: Position 0 Reached! Phase One Complete. Will now begin Phase 2: Cleaning.")
            row = 0
            col = 0
            if(dirty):
                print("\tAgent: Found a dirty square... GROSS... Cleaning now")
                return "suck"
            else: 
                print("\tAgent: Moving to next corner!")
                return "east"
        if(bumpers.get("north") == False):
            print("\tAgent: Moving to Position 0 (Northwest Corner)\n\tMoving...")
            return "north"
        elif(bumpers.get("west") == False):
            print("\tAgent: Moving to Position 0 (Northwest Corner)\n\tMoving...")
            return "west"

    else: 
        if(dirty):
            print("\tAgent: Found a dirty square... GROSS... Cleaning now")
            cleaned.append([row, col])
            return "suck"
        else:
            if(not(bumpers.get(direction))):
                if(direction == "east"):
                    print("\tAgent: Moving to east wall")
                    col += 1
                else:
                    print("\tAgent: Moving to west wall")
                    col -= 1
                return direction
            else:
                if(direction == "east"):
                    print("\tAgent: Wall reached! Moving south and continuing west.")
                    direction = "west"
                else:
                    print("\tAgent: Wall reached! Moving south and continuing east.")
                    direction = "east"
                row += 1
                return "south"


    

        moving = True




In [12]:
simulation_environment(Model_Based_Reflex, 5)

Number of dirty squares:
3
{'north': False, 'south': False, 'west': False, 'east': False}
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 0 - action: north  position: ( 2 , 2 )
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 1 - action: north  position: ( 2 , 1 )
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 2 - action: west  position: ( 2 , 0 )
	Agent: Moving to Position 0 (Northwest Corner)
	Moving...
Environment: Step 3 - action: west  position: ( 1 , 0 )
	Agent: Position 0 Reached! Phase One Complete. Will now begin Phase 2: Cleaning.
	Agent: Moving to next corner!
Environment: Step 4 - action: east  position: ( 0 , 0 )
	Agent: Moving to east wall
Environment: Step 5 - action: east  position: ( 1 , 0 )
	Agent: Moving to east wall
Environment: Step 6 - action: east  position: ( 2 , 0 )
	Agent: Found a dirty square... GROSS... Cleaning now
Environment: Step 7 - action: suck  position: ( 3 , 0 )
	

3

## Task 4: Simulation study [30 Points]

Compare the performance (the performance measure is defined in the PEAS description above) of the agents using  environments of different size. E.g., $5 \times 5$, $10 \times 10$ and
$100 \times 100$. Use 100 random runs for each. Present the results using tables and graphs. Discuss the differences between the agents. 
([Help with charts and tables in Python](https://github.com/mhahsler/CS7320-AI/blob/master/Python_Code_Examples/charts_and_tables.ipynb))

In [13]:
# Your code goes here
import seaborn as sns

In [ ]:
environment_sizes = [5, 10, 100]

simple_random = []
simple_reflex = []
model_reflex = []

for x in range(100):
    n = np.random.choice(environment_sizes)
    simple_random.append([n, simulation_environment(simple_randomized_agent, n)])
    simple_reflex.append([n, simulation_environment(simple_reflex_agent, n)])
    model_reflex.append([n, simulation_environment(Model_Based_Reflex, n)])
    


Number of dirty squares:
1960
{'north': False, 'south': False, 'west': False, 'east': False}
Environment: Step 0 - action: east  position: ( 27 , 7 )
Environment: Step 1 - action: west  position: ( 28 , 7 )
Environment: Step 2 - action: south  position: ( 27 , 7 )
Environment: Step 3 - action: south  position: ( 27 , 8 )
Environment: Step 4 - action: west  position: ( 27 , 9 )
Environment: Step 5 - action: west  position: ( 26 , 9 )
Environment: Step 6 - action: east  position: ( 25 , 9 )
Environment: Step 7 - action: suck  position: ( 26 , 9 )
Environment: Step 8 - action: north  position: ( 26 , 9 )
Environment: Step 9 - action: east  position: ( 26 , 8 )
Environment: Step 10 - action: north  position: ( 27 , 8 )
Environment: Step 11 - action: west  position: ( 27 , 7 )
Environment: Step 12 - action: west  position: ( 26 , 7 )
Environment: Step 13 - action: north  position: ( 25 , 7 )
Environment: Step 14 - action: east  position: ( 25 , 6 )
Environment: Step 15 - action: south  posi

Environment: Step 246 - action: south  position: ( 43 , 8 )
Environment: Step 247 - action: west  position: ( 43 , 9 )
Environment: Step 248 - action: east  position: ( 42 , 9 )
Environment: Step 249 - action: west  position: ( 43 , 9 )
Environment: Step 250 - action: east  position: ( 42 , 9 )
Environment: Step 251 - action: south  position: ( 43 , 9 )
Environment: Step 252 - action: west  position: ( 43 , 10 )
Environment: Step 253 - action: north  position: ( 42 , 10 )
Environment: Step 254 - action: south  position: ( 42 , 9 )
Environment: Step 255 - action: north  position: ( 42 , 10 )
Environment: Step 256 - action: west  position: ( 42 , 9 )
Environment: Step 257 - action: east  position: ( 41 , 9 )
Environment: Step 258 - action: south  position: ( 42 , 9 )
Environment: Step 259 - action: south  position: ( 42 , 10 )
Environment: Step 260 - action: north  position: ( 42 , 11 )
Environment: Step 261 - action: south  position: ( 42 , 10 )
Environment: Step 262 - action: north  po

Environment: Step 468 - action: south  position: ( 42 , 13 )
Environment: Step 469 - action: east  position: ( 42 , 14 )
Environment: Step 470 - action: north  position: ( 43 , 14 )
Environment: Step 471 - action: south  position: ( 43 , 13 )
Environment: Step 472 - action: south  position: ( 43 , 14 )
Environment: Step 473 - action: north  position: ( 43 , 15 )
Environment: Step 474 - action: west  position: ( 43 , 14 )
Environment: Step 475 - action: south  position: ( 42 , 14 )
Environment: Step 476 - action: north  position: ( 42 , 15 )
Environment: Step 477 - action: west  position: ( 42 , 14 )
Environment: Step 478 - action: north  position: ( 41 , 14 )
Environment: Step 479 - action: south  position: ( 41 , 13 )
Environment: Step 480 - action: east  position: ( 41 , 14 )
Environment: Step 481 - action: west  position: ( 42 , 14 )
Environment: Step 482 - action: south  position: ( 41 , 14 )
Environment: Step 483 - action: suck  position: ( 41 , 15 )
Environment: Step 484 - action

Environment: Step 690 - action: south  position: ( 46 , 9 )
Environment: Step 691 - action: south  position: ( 46 , 10 )
Environment: Step 692 - action: suck  position: ( 46 , 11 )
Environment: Step 693 - action: north  position: ( 46 , 11 )
Environment: Step 694 - action: north  position: ( 46 , 10 )
Environment: Step 695 - action: south  position: ( 46 , 9 )
Environment: Step 696 - action: north  position: ( 46 , 10 )
Environment: Step 697 - action: north  position: ( 46 , 9 )
Environment: Step 698 - action: north  position: ( 46 , 8 )
Environment: Step 699 - action: east  position: ( 46 , 7 )
Environment: Step 700 - action: suck  position: ( 47 , 7 )
Environment: Step 701 - action: east  position: ( 47 , 7 )
Environment: Step 702 - action: south  position: ( 48 , 7 )
Environment: Step 703 - action: suck  position: ( 48 , 8 )
Environment: Step 704 - action: south  position: ( 48 , 8 )
Environment: Step 705 - action: east  position: ( 48 , 9 )
Environment: Step 706 - action: south  po

Environment: Step 912 - action: north  position: ( 66 , 15 )
Environment: Step 913 - action: south  position: ( 66 , 14 )
Environment: Step 914 - action: east  position: ( 66 , 15 )
Environment: Step 915 - action: west  position: ( 67 , 15 )
Environment: Step 916 - action: south  position: ( 66 , 15 )
Environment: Step 917 - action: east  position: ( 66 , 16 )
Environment: Step 918 - action: suck  position: ( 67 , 16 )
Environment: Step 919 - action: north  position: ( 67 , 16 )
Environment: Step 920 - action: south  position: ( 67 , 15 )
Environment: Step 921 - action: suck  position: ( 67 , 16 )
Environment: Step 922 - action: west  position: ( 67 , 16 )
Environment: Step 923 - action: suck  position: ( 66 , 16 )
Environment: Step 924 - action: east  position: ( 66 , 16 )
Environment: Step 925 - action: east  position: ( 67 , 16 )
Environment: Step 926 - action: east  position: ( 68 , 16 )
Environment: Step 927 - action: west  position: ( 69 , 16 )
Environment: Step 928 - action: wes

...

Environment: Step 59213 - action: east  position: ( 77 , 49 )
Environment: Step 59214 - action: south  position: ( 78 , 49 )
Environment: Step 59215 - action: north  position: ( 78 , 50 )
Environment: Step 59216 - action: west  position: ( 78 , 49 )
Environment: Step 59217 - action: north  position: ( 77 , 49 )
Environment: Step 59218 - action: north  position: ( 77 , 48 )
Environment: Step 59219 - action: south  position: ( 77 , 47 )
Environment: Step 59220 - action: east  position: ( 77 , 48 )
Environment: Step 59221 - action: suck  position: ( 78 , 48 )
Environment: Step 59222 - action: east  position: ( 78 , 48 )
Environment: Step 59223 - action: suck  position: ( 79 , 48 )
Environment: Step 59224 - action: east  position: ( 79 , 48 )
Environment: Step 59225 - action: east  position: ( 80 , 48 )
Environment: Step 59226 - action: suck  position: ( 81 , 48 )
Environment: Step 59227 - action: suck  position: ( 81 , 48 )
Environment: Step 59228 - action: west  position: ( 81 , 48 )
Env

Environment: Step 59435 - action: west  position: ( 70 , 48 )
Environment: Step 59436 - action: south  position: ( 69 , 48 )
Environment: Step 59437 - action: west  position: ( 69 , 49 )
Environment: Step 59438 - action: east  position: ( 68 , 49 )
Environment: Step 59439 - action: suck  position: ( 69 , 49 )
Environment: Step 59440 - action: suck  position: ( 69 , 49 )
Environment: Step 59441 - action: west  position: ( 69 , 49 )
Environment: Step 59442 - action: west  position: ( 68 , 49 )
Environment: Step 59443 - action: south  position: ( 67 , 49 )
Environment: Step 59444 - action: south  position: ( 67 , 50 )
Environment: Step 59445 - action: north  position: ( 67 , 51 )
Environment: Step 59446 - action: east  position: ( 67 , 50 )
Environment: Step 59447 - action: east  position: ( 68 , 50 )
Environment: Step 59448 - action: west  position: ( 69 , 50 )
Environment: Step 59449 - action: east  position: ( 68 , 50 )
Environment: Step 59450 - action: west  position: ( 69 , 50 )
Envi

Environment: Step 59602 - action: south  position: ( 60 , 49 )
Environment: Step 59603 - action: north  position: ( 60 , 50 )
Environment: Step 59604 - action: south  position: ( 60 , 49 )
Environment: Step 59605 - action: south  position: ( 60 , 50 )
Environment: Step 59606 - action: suck  position: ( 60 , 51 )
Environment: Step 59607 - action: north  position: ( 60 , 51 )
Environment: Step 59608 - action: north  position: ( 60 , 50 )
Environment: Step 59609 - action: north  position: ( 60 , 49 )
Environment: Step 59610 - action: west  position: ( 60 , 48 )
Environment: Step 59611 - action: suck  position: ( 59 , 48 )
Environment: Step 59612 - action: south  position: ( 59 , 48 )
Environment: Step 59613 - action: west  position: ( 59 , 49 )
Environment: Step 59614 - action: south  position: ( 58 , 49 )
Environment: Step 59615 - action: east  position: ( 58 , 50 )
Environment: Step 59616 - action: east  position: ( 59 , 50 )
Environment: Step 59617 - action: east  position: ( 60 , 50 )

Environment: Step 59758 - action: south  position: ( 58 , 52 )
Environment: Step 59759 - action: suck  position: ( 58 , 53 )
Environment: Step 59760 - action: east  position: ( 58 , 53 )
Environment: Step 59761 - action: south  position: ( 59 , 53 )
Environment: Step 59762 - action: west  position: ( 59 , 54 )
Environment: Step 59763 - action: east  position: ( 58 , 54 )
Environment: Step 59764 - action: suck  position: ( 59 , 54 )
Environment: Step 59765 - action: north  position: ( 59 , 54 )
Environment: Step 59766 - action: east  position: ( 59 , 53 )
Environment: Step 59767 - action: north  position: ( 60 , 53 )
Environment: Step 59768 - action: east  position: ( 60 , 52 )
Environment: Step 59769 - action: south  position: ( 61 , 52 )
Environment: Step 59770 - action: east  position: ( 61 , 53 )
Environment: Step 59771 - action: east  position: ( 62 , 53 )
Environment: Step 59772 - action: suck  position: ( 63 , 53 )
Environment: Step 59773 - action: west  position: ( 63 , 53 )
Env

Environment: Step 59924 - action: west  position: ( 63 , 56 )
Environment: Step 59925 - action: suck  position: ( 62 , 56 )
Environment: Step 59926 - action: south  position: ( 62 , 56 )
Environment: Step 59927 - action: west  position: ( 62 , 57 )
Environment: Step 59928 - action: west  position: ( 61 , 57 )
Environment: Step 59929 - action: west  position: ( 60 , 57 )
Environment: Step 59930 - action: south  position: ( 59 , 57 )
Environment: Step 59931 - action: east  position: ( 59 , 58 )
Environment: Step 59932 - action: east  position: ( 60 , 58 )
Environment: Step 59933 - action: west  position: ( 61 , 58 )
Environment: Step 59934 - action: suck  position: ( 60 , 58 )
Environment: Step 59935 - action: south  position: ( 60 , 58 )
Environment: Step 59936 - action: north  position: ( 60 , 59 )
Environment: Step 59937 - action: suck  position: ( 60 , 58 )
Environment: Step 59938 - action: west  position: ( 60 , 58 )
Environment: Step 59939 - action: east  position: ( 59 , 58 )
Envi

In [ ]:
import matplotlib.pyplot as plt
zip(*simple_random)
zip(*simple_reflex)
zip(*model_reflex)

Fill out the following table with the average performance measure for 100 random runs (you may also create this table with code):

| Size     | Randomized Agent | Simple Reflex Agent | Model-based Reflex Agent |
|----------|------------------|---------------------|--------------------------|
| 5x5     | | | |
| 10x10   | | | |
| 100x100 | | | |

Add charts to compare the performance of the different agents.

In [ ]:
# Your graphs and discussion of the results goes here

## Task 5: Robustness of the agent implementations [10 Points] 

Describe how **your agent implementations** will perform 

* if it is put into a rectangular room with unknown size, 
* if the cleaning area can have an iregular shape (e.g., a hallway connecting two rooms), or 
* if the room contains obstacles (i.e., squares that it cannot pass through and trigger the bumper sensors).

In [ ]:
# Answer goes here
# https://www.explainthatstuff.com/how-roomba-works.html
# Roombas work by wall following and wall bouncing (aka randomly cleaning until an object is hit...)

## Graduate student advanced task: Obstacles [10 Points]

__Undergraduate students:__ This is a bonus task you can attempt if you like [+5 Bonus Points].

1. Change your simulation environment tor run experiments for the following problem: Add random obstacle squares that also trigger the bumper sensor. The agent does not know where the obstacles are. Observe how this changes the performance of the three implementations.

2. Describe what would need to be done to perform better with obstacles. Add code if you can. 

In [ ]:
# Your code and discussion goes here

## More advanced implementation tasks

* __Agent for and environment with obstacles:__ Implement an agent for an environment where the agent does not know how large the environment is (we assume it is rectangular), where it starts or where the obstacles are. An option would be to always move to the closest unchecked/uncleaned square (note that this is actualy depth-first search).

* __Utility-based agent:__ Change the environment for a $5 \times 5$ room, so each square has a fixed probability of getting dirty again. For the implementation, we give the environment a 2-dimensional array of probabilities. The utility of a state is defined as the number of currebntly clean squares in the room. Implement a utility-based agent that maximizes the expected utility over one full charge which lasts for 100000 time steps. To do this, the agent needs to learn the probabilities with which different squares get dirty again. This is very tricky!

In [ ]:
# Your ideas/code